# Data Import & Preprocessing

In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVR
!pip install feature_engine
from feature_engine.creation import CyclicalFeatures
from sklearn.decomposition import PCA
from sklearn.metrics import r2_score,mean_absolute_error, mean_squared_error
import numpy as np
from google.colab import drive
import math
from sklearn.preprocessing import PolynomialFeatures


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
drive.mount('/content/drive/', force_remount=True)
fileName = "/content/drive/My Drive/Dataset.xlsx"
df_Labels = pd.read_excel(fileName, sheet_name="Plant_1_Data")
df_Labels = df_Labels.drop(['PLANT_ID'], axis=1)
df_Labels["DATE_TIME"] = pd.to_datetime(df_Labels.DATE_TIME)
df_Features = pd.read_excel(fileName, sheet_name="Plant_1_Sensor_Data")
df_Features = df_Features.drop(['PLANT_ID','SOURCE_KEY'], axis=1)
df_Features['DATE_TIME'] = pd.to_datetime(df_Features.DATE_TIME)
print(df_Features.head())

Mounted at /content/drive/
            DATE_TIME  AMBIENT_TEMPERATURE  MODULE_TEMPERATURE  IRRADIATION
0 2020-05-15 00:00:00            25.184316           22.857507          0.0
1 2020-05-15 00:15:00            25.084589           22.761668          0.0
2 2020-05-15 00:30:00            24.935753           22.592306          0.0
3 2020-05-15 00:45:00            24.846130           22.360852          0.0
4 2020-05-15 01:00:00            24.621525           22.165423          0.0


In [ ]:
df_Learn = pd.merge(df_Features, df_Labels, how='inner', left_on = ['DATE_TIME'], right_on = ['DATE_TIME'])
df_Learn.describe()

AMBIENT_TEMPERATURE  MODULE_TEMPERATURE   IRRADIATION      DC_POWER  \
count         45680.000000        45680.000000  45680.000000  45680.000000   
mean             25.917168           31.877975      0.236834   3197.175971   
std               3.556550           12.638448      0.306316   4080.448523   
min              20.398505           18.140415      0.000000      0.000000   
25%              22.930031           21.406390      0.000000      0.000000   
50%              24.993020           25.379072      0.035266    464.196429   
75%              28.379008           42.757119      0.459503   6478.424107   
max              35.252486           65.545714      1.221652  14471.125000   

           AC_POWER   DAILY_YIELD   TOTAL_YIELD  
count  45680.000000  45680.000000  4.568000e+04  
mean     312.652679   3313.146538  6.957007e+06  
std      398.668968   3156.100252  4.172386e+05  
min        0.000000      0.000000  6.183645e+06  
25%        0.000000      0.000000  6.512358e+06  
50%       44.912500   2653.633928  7.115711e+06  
75%      634.481250   6318.000000  7.244521e+06  
max     1410.950000   9163.000000  7.846821e+06

In [ ]:
'''sourceKeyList = list(df_Learn['SOURCE_KEY'].unique())
sourceKeyDict = {}
for key in sourceKeyList:
  df_Key = df_Learn[df_Learn['SOURCE_KEY'] == key]
  #print(df_Key.describe())
  X = df_Key.drop(['DC_POWER', 'AC_POWER', 'DAILY_YIELD', 'TOTAL_YIELD', 'SOURCE_KEY'], axis = 1)
  #print(X.describe())
  y = df_Key['DC_POWER']
  
  #Train Val Test Split: 80%, 10%, 10%
  X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1, random_state=42)
  X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=1/9, random_state=42)
  #print(X_train.head()) print(y_train)
  sourceKeyDict[key] = list([X_train, y_train, X_val, y_val, X_test, y_test])
len(sourceKeyDict)
'''
Data_X = df_Learn.drop(['DC_POWER', 'AC_POWER', 'DAILY_YIELD', 'TOTAL_YIELD', 'SOURCE_KEY'], axis = 1)
Data_X["Hour"] =Data_X["DATE_TIME"].dt.hour
Data_X["Minute"]=Data_X["DATE_TIME"].dt.minute
Data_X=Data_X.drop(["DATE_TIME"],axis=1)
y = np.log(df_Learn['DC_POWER'] + 1)
X_train, X_test, y_train, y_test = train_test_split(Data_X, y, test_size=0.1, random_state=42)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=1/9, random_state=42)
Scaler = StandardScaler()

column_to_scale =["AMBIENT_TEMPERATURE","MODULE_TEMPERATURE","IRRADIATION"]
Scaler.fit(X_train[column_to_scale])
X_train[column_to_scale] = Scaler.transform(X_train[column_to_scale])
X_test[column_to_scale] = Scaler.transform(X_test[column_to_scale])
X_val[column_to_scale] = Scaler.transform(X_val[column_to_scale])
display(X_val.head(), X_test.head(), X_train.shape)


AMBIENT_TEMPERATURE  MODULE_TEMPERATURE  IRRADIATION  Hour  Minute
17778            -0.295912           -0.304658    -0.101646     7      15
13601            -0.842882           -0.826884    -0.771859     5       0
30013             0.654863            2.293684     2.893856    12      30
26823             2.018994            1.203059     0.793598    15      45
30658            -0.074950           -0.664980    -0.771859    20       0

AMBIENT_TEMPERATURE  MODULE_TEMPERATURE  IRRADIATION  Hour  Minute
29503            -1.213483           -0.786463    -0.498765     6      45
45488            -0.779360           -0.769684    -0.771859    21      45
40219             0.139353            0.962153     1.394654     9      15
7270              0.507589            0.843659     0.351929    14      15
15418            -1.129263           -0.896089    -0.771859     2      45

(36544, 5)

# Feature Manipulation

In [ ]:
#df_Learn["Hour"] = df_Learn.DATE_TIME.dt.hour
#df_Learn["Minute"] = df_Learn.DATE_TIME.dt.minute
cyclical = CyclicalFeatures(variables=["Hour","Minute"], drop_original=True)
cyclical.fit(X_train)
X_train = cyclical.transform(X_train)
X_test = cyclical.transform(X_test)
X_val = cyclical.transform(X_val)
display(X_train)

AMBIENT_TEMPERATURE  MODULE_TEMPERATURE  IRRADIATION  Hour_sin  \
44297            -0.525323           -0.019621     0.080730  0.816970   
12926            -0.422765           -0.772043    -0.771859 -0.519584   
13841            -0.303859            0.157139     0.356189  0.942261   
7419              0.537236            0.703588     0.576141 -0.942261   
44849             0.802179            0.865840     1.143715 -0.631088   
...                    ...                 ...          ...       ...   
41771            -0.958424           -0.827799    -0.771859  0.730836   
38424            -0.149259            0.231640     1.109672 -0.398401   
38429            -0.149259            0.231640     1.109672 -0.398401   
33692            -1.294380           -0.945511    -0.606810  0.997669   
45415            -0.849500           -0.849130    -0.771859 -0.730836   

       Hour_cos    Minute_sin  Minute_cos  
44297 -0.576680  8.660254e-01        -0.5  
12926  0.854419 -8.660254e-01        -0.5  
13841 -0.334880 -2.449294e-16         1.0  
7419  -0.334880  0.000000e+00         1.0  
44849 -0.775711 -8.660254e-01        -0.5  
...         ...           ...         ...  
41771  0.682553  0.000000e+00         1.0  
38424 -0.917211  0.000000e+00         1.0  
38429 -0.917211  0.000000e+00         1.0  
33692 -0.068242 -8.660254e-01        -0.5  
45415  0.682553 -2.449294e-16         1.0  

[36544 rows x 7 columns]

In [ ]:
poly = PolynomialFeatures(degree=2, interaction_only = True)
poly.fit(X_train)
X_train = pd.DataFrame(poly.transform(X_train))
X_test = pd.DataFrame(poly.transform(X_test))
X_val = pd.DataFrame(poly.transform(X_val))
display(X_train.shape)

(36544, 29)

In [ ]:

'''pca_2 = PCA(n_components=2, random_state=42)
pca_2.fit(X_train)
x_pca_2 = pca_2.transform(X_train)
#pca_2.transform(X_test)
plt.figure(figsize=(10,7))
#sns.set(rc={'figure.figsize':(100,100)})'''
import plotly.express as px
from sklearn.decomposition import PCA

df = X_train
features = X_train.columns

pca = PCA(n_components=20)
pca.fit(X_train)
components_train = pca.transform(X_train)
components_test = pca.transform(X_test)
components_val = pca.transform(X_val)
labels = {
    str(i): f"PC {i+1} ({var:.1f}%)"
    for i, var in enumerate(pca.explained_variance_ratio_ * 100)
}

fig = px.scatter_matrix(
    components_train,
    labels=labels,
    dimensions=range(10), width=1920, height=1080
)
fig.update_traces(diagonal_visible=False)

fig.show()
#fig.write_image("PCA.png")
'''fig, ax = pyplot.subplots(figsize=(10,10))
sns.scatterplot(ax = ax, a=x_pca_2[:,0], b=x_pca_2[:, 1], s=70 , palette=['green','blue'])
plt.title("2D Scatterplot of dataset", pad = 15)
plt.xlabel("First principal component")
plt.ylabel("Second principal component")
plt.savefig("2d_scatterplot.png")
plt.plot(np.cumsum(pca_2.explained_variance_ratio_))
plt.xlabel('Number of components')
plt.ylabel('Explained variance')
plt.savefig('Plot', dpi=100)'''

'fig, ax = pyplot.subplots(figsize=(10,10))\nsns.scatterplot(ax = ax, a=x_pca_2[:,0], b=x_pca_2[:, 1], s=70 , palette=[\'green\',\'blue\'])\nplt.title("2D Scatterplot of dataset", pad = 15)\nplt.xlabel("First principal component")\nplt.ylabel("Second principal component")\nplt.savefig("2d_scatterplot.png")\nplt.plot(np.cumsum(pca_2.explained_variance_ratio_))\nplt.xlabel(\'Number of components\')\nplt.ylabel(\'Explained variance\')\nplt.savefig(\'Plot\', dpi=100)'

# Model Training

In [ ]:
'''from sklearn.model_selection import cross_val_score
from sklearn.model_selection import validation_curve
parameter_range=parameter_range = np.arange(1, 10, 1)
SupportVectorRegModel = SVR(kernel='rbf', C = 8.0 , gamma = 0.2 , epsilon= 0.1)
#SupportVectorRegModel = SVR()
SupportVectorRegModel.fit(X_train,y_train)
display(cross_val_score(SupportVectorRegModel, X_train, y_train))
pred = SupportVectorRegModel.predict(X_test)
pred[pred<0]=0.0
display(pd.DataFrame(np.exp(pred)+1).describe())
display(pd.DataFrame(np.exp(y_test)+1).describe())
display(SupportVectorRegModel.score(X_test , y_test,sample_weight=None))'''

#from sklearn.metrics import accuracy_score
#import matplotlib.pyplot as plt
class SVR:
  
  def __init__(self, Epsilon=0.1):
    self.w = None
    self.epsilon = Epsilon
    self.b = None
    
  def model(self, x):
    #print(x, self.w)
    return (np.dot(self.w, x.transpose())+ self.b) 
    
  def predict(self, X):
    
    Y = []
    for x in X:
      # print(x)
      result = self.model(x)
      Y.append(result)
    
    return np.array(Y)
  
  def fit(self, X, Y, epochs = 100, lr = 0.001, early_stopping = False, tol = 0.00001, tol_epoch = 5, norm=None, Lambda=1.0):
    
    early_stop_count=0
    self.w = np.ones(X.shape[1])
    self.b = 0
    val_loss = math.inf
    min_val_loss=math.inf
    #print(X.shape)
    for i in range(epochs):
      prev_val_loss = val_loss
      #print(prev_val_loss)
      for x, y in zip(X, Y):
        y_pred = self.model(x)
        #print(len())
        if np.abs(y_pred - y) >= self.epsilon:
          #print("Hi")
          #self.w = self.w - lr * np.log((y_pred + 1)/(y + 1)) * (x/(y_pred + 1))
          if norm == 'L1':
            for w in self.w:
              if(w >= 0):
                w = w + lr * (y - y_pred) * x + Lambda 
              else:
                w = w + lr * (y - y_pred) * x - Lambda
                self.b = self.b + lr * (y - y_pred) - Lambda
            if self.b >= 0:
              self.b = self.b + lr * (y - y_pred) + Lambda
            else:
              self.b = self.b + lr * (y - y_pred) - Lambda
          elif norm == 'L2':
            self.w = self.w + lr * (y - y_pred) * x + (Lambda * self.w)
            self.b = self.b + lr * (y - y_pred) + (Lambda * self.b)
          else:
            self.w = self.w + lr * (y - y_pred) * x
            self.b = self.b + lr * (y - y_pred)
      #print(i)
      if early_stopping:
        val_pred = self.predict(X_val.values)
        val_loss = np.sum(np.abs(val_pred - y_val))
        #print(val_loss)
        
        if val_loss < min_val_loss:
          min_val_loss=val_loss
          chkptw = self.w
          #print(min_val_loss)
        if val_loss - prev_val_loss > tol:
          early_stop_count += 1
        if early_stop_count > tol_epoch:
          print(i)
          break
        self.w = chkptw

svr=SVR(Epsilon=0.05)
svr.fit(X_train.values, y_train.values, epochs = 500, lr = 0.0001, early_stopping=True, tol_epoch=10, tol=0.0001 )
pred = svr.predict(X_test.values)
mae = mean_absolute_error(y_test, pred)
display(mae)

76


0.8229279765670986

In [ ]:
display(mean_absolute_error(y_train, svr.predict(components_train)))

In [ ]:
from scipy.sparse.linalg.isolve.minres import sqrt
from sklearn.metrics import mean_squared_error
mae = mean_absolute_error(y_test, pred)
display(mae)
display(np.exp(mae))
mse = mean_squared_error(y_test, pred)
display((mse))
rmse=sqrt(mse)
display((rmse))

0.8309669481660541

2.29553733307352

1.2144805453425285

1.1020347296444557

In [ ]:
vals = pd.DataFrame([[pd.to_datetime('2020-05-15 12:30:00'), '32.14768473',	'52.35325513',	'0.6492476293']], columns=('DATE_TIME', 'AMBIENT_TEMPERATURE', 'MODULE_TEMPERATURE', 'IRRADIATION'))
#display(vals)
vals['Hour'] = vals['DATE_TIME'].dt.hour
vals['Minute'] = vals['DATE_TIME'].dt.minute
vals = vals.drop(['DATE_TIME'], axis = 1)
display(vals)
vals[column_to_scale] = Scaler.transform(vals[column_to_scale])
#display(vals)
vals = cyclical.transform(vals)
vals = pd.DataFrame(poly.transform(vals))
vals = pca.transform(vals)
#display(vals)
display("DC_POWER Prediction for sample: " + str(np.exp(svr.predict(vals))+1))

In [ ]:
display("Size of samples: " + str(len(y_test)))
#Variance check for two tailed test
display("Variance of Predicted Samples: " + str(np.var((pred))), "Variance of Ground Truth: " + str(np.var(y_test)))
display("Standard Deviation of the Sample: " + str(np.exp(np.sqrt(np.var(pred)))))
#Ratio
display("Ratio to check for nearly equal Variance: " + str(np.var(y_test)/np.var(pred)))

'Size of samples: 4568'

'Variance of Predicted Samples: 16.073796305951532'

'Variance of Ground Truth: 17.676883353868018'

'Standard Deviation of the Sample: 55.10353808627488'

'Ratio to check for nearly equal Variance: 1.0997329453106808'

In [ ]:
#T-Test
#Equal Variance, hence equal_var = 'True'
import scipy.stats as stats
y_pred = svr.predict(X_test.values)
tstat, t_pval = stats.ttest_ind(a=y_test, b=y_pred, equal_var=False)

display("T-Statistic: " + str(tstat.round(3)), "PValue: " + str(t_pval.round(3)))

'T-Statistic: 0.658'

'PValue: 0.511'